# Setup UI

In [1]:
import os
import json

# If the file does not exist it'll default to the manual setting see below
filePathToSettingsFile = '../../env/ai.json'

# Is there a settings file? 
if os.path.exists(filePathToSettingsFile):
    # Yes there is so load settings from there
    
    print(f'Loading settings from {filePathToSettingsFile}')
    f = open(filePathToSettingsFile)
    settingsJson = json.load(f)
    del f

    for key in settingsJson:
        os.environ[key] = settingsJson[key]
        
    del settingsJson
else:        
    # Set variables manually
    
    print('Setting variables manually as there is not ai.json settings file')

    # Update the variables below with your own settings
    os.environ['REQUESTS_CA_BUNDLE'] = '../../env/ZCert.pem'    
    os.environ['HUGGING_FACE_API_KEY'] = 'Get here: https://huggingface.co/settings/tokens'
    os.environ['OPENAI_API_KEY'] = 'Get here: https://platform.openai.com/account/api-keys'
    os.environ["SERPAPI_API_KEY"] = 'serpapi KEY, Get here: https://serpapi.com/manage-api-key'    

Loading settings from ../../env/ai.json


In [2]:
import os
import pinecone
from langchain.chains import RetrievalQA
from langchain.embeddings import OpenAIEmbeddings
from langchain.llms import OpenAI
from langchain.vectorstores import Pinecone
import gradio as gr

c:\sc\ai\rag-demo-1\.venv\lib\site-packages\pinecone\index.py:4: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from tqdm.autonotebook import tqdm


In [9]:
embeddings = OpenAIEmbeddings()

course = "Roman History"
if course == "Roman History":
    print(f"Using course: {course}")
    pinecone.init(api_key=os.environ["PINECONE_API_KEY_2"], environment=os.environ["PINECONE_API_ENV_2"])
    index = pinecone.Index("rag-demo-1-history-rome")
    vector_store = Pinecone(index, embeddings, "text")
    
query = "When was Ceasar born?"

result = vector_store.similarity_search(
    query,  # our search query
    k=1  # return 3 most relevant docs
)

print(result[0])

Using course: Roman History
page_content='The situation in Rome. While Pompey was adding to his\nmilitary reputation in the East he was regarded with jealous\nand anxious eyes not only by the Senate but also by the other\nchampions of the popular party, Crassus who found his wealth\nno match for Pompeys military achievements, and Caius Julius\nCaesar who was rapidly coming to be one of the leading figures in\nRoman public life. Caesar was born in 100 B. C., of the patrician [162]\ngens of the Julii, but since his aunt was the wife of Marius,\nand he himself had married the daughter of Cinna, his lot was\ncast with the Populares. As a young man he had distinguished\nhimself by refusing to divorce his wife at Sullas behest, whereat\nSulla was with difficulty induced to spare his life, saying that he\nsaw in him many a Marius. For the time being Caesar judged it\nprudent to withdraw from Rome to Rhodes. While in the East\nhe was captured by pirates, and after being ransomed, fulfilled' me

In [6]:
llm = OpenAI(temperature=0)
llm.predict("Hello there")

'\n\nHow are you?'

In [21]:
from langchain.memory import ConversationBufferMemory
from langchain.chains import ConversationalRetrievalChain

memory = ConversationBufferMemory(memory_key="chat_history", return_messages= True)
chain = ConversationalRetrievalChain.from_llm(llm, retriever= vector_store.as_retriever(), memory= memory)

In [26]:
query = """ 
    SYSTEM:
    You are a helpful teacher who is teaching a class of 10 year olds. 
    Your answers must only come from the context provided to you in the question.
    If you don't know the answer then say so. 
    The answers should be at least 40 words or longer
    
    QUESTION:
    What is moby dick?
    
"""
chain.run({'question': query})

" I don't know."

In [5]:
qa = RetrievalQA.from_chain_type(llm=llm, chain_type="stuff", retriever=vector_store.as_retriever())

query = input("Who was ceasar and why whas he noteable?")
answer = qa.run(query)


qa = RetrievalQA.from_chain_type(llm, chain_type="stuff", retriever=retriever)
response = qa.run(query)

# print(answer)
# print("\nWhat else can I help you with:")

# while True:
#     query = input("Who was ceasar and why whas he notable?")
#     answer = qa.run(query)
#     print(answer)
#     print("\nWhat else can I help you with:")

KeyboardInterrupt: Interrupted by user

In [ ]:
qa = RetrievalQA.from_chain_type(llm=OpenAI(temperature=0), chain_type="stuff", retriever=vector_store.as_retriever())

print("Connector development help bot. What do you want to know?")
while True:
    query = input("")
    answer = qa.run(query)
    print(answer)
    print("\nWhat else can I help you with:")

In [3]:
def ask_question(openAIKey, prompt, question):
    return "Your question is " + question + "!!"

iface = gr.Interface(fn=ask_question, 
                     inputs=[
                            gr.Textbox(label="OpenAI Key", placeholder="Paste your OpenAI key here"),
                            gr.TextArea(label="Prompt"), 
                            gr.TextArea(label="Question", placeholder="Type your question here, it will get injected into the prompt at QUESTION"),
                            ],
                     outputs="text")

iface.launch()

Running on local URL:  http://127.0.0.1:7860

To create a public link, set `share=True` in `launch()`.
